## Обучение генеративной трансформерной модели с помощью `transformers`

Для 

In [83]:
%pip install --upgrade git+https://github.com/dask/s3fs

Defaulting to user installation because normal site-packages is not writeable
  Cloning https://github.com/dask/s3fs to /tmp/pip-req-build-y1s77er1
  Running command git clone --filter=blob:none --quiet https://github.com/dask/s3fs /tmp/pip-req-build-y1s77er1
  Resolved https://github.com/dask/s3fs to commit 2c074502c2d6a9be0d3f05eb678f4cc5add2e7e5
  Preparing metadata (setup.py) ... done
  Obtaining dependency information for aiobotocore~=2.7.0 from https://files.pythonhosted.org/packages/d0/bc/6a96a686845c9f5958fac0ecafa6050ed77d0e71553b3cfe69acbaa70191/aiobotocore-2.7.0-py3-none-any.whl.metadata
  Obtaining dependency information for fsspec==2023.10.0 from https://files.pythonhosted.org/packages/e8/f6/3eccfb530aac90ad1301c582da228e4763f19e719ac8200752a4841b0b2d/fsspec-2023.10.0-py3-none-any.whl.metadata
  Obtaining dependency information for botocore<1.31.65,>=1.31.16 from https://files.pythonhosted.org/packages/d0/68/6a9c405bc6c6e7d832743a458c87f21cee393ef2cf32437a0a3a07cd0ae9/boto

In [16]:
%pip install transformers tokenizers datasets evaluate accelerate

Defaulting to user installation because normal site-packages is not writeable
  Obtaining dependency information for accelerate from https://files.pythonhosted.org/packages/d9/92/2d3aecf9f4a192968035880be3e2fc8b48d541c7128f7c936f430d6f96da/accelerate-0.23.0-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 258.1/258.1 kB 2.2 MB/s eta 0:00:00
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2023.6.0 requires fsspec==2023.6.0, but you have fsspec 2023.10.0 which is incompatible.

[notice] A new release of pip is available: 23.2.1 -> 23.3.1
[notice] To update, run: python3 -m pip install --upgrade pip


In [2]:
urls = ['http://az.lib.ru/t/tolstoj_lew_nikolaewich/text_0039.shtml',
        'http://az.lib.ru/t/tolstoj_lew_nikolaewich/text_0040.shtml',
        'http://az.lib.ru/t/tolstoj_lew_nikolaewich/text_0050.shtml',
        'http://az.lib.ru/t/tolstoj_lew_nikolaewich/text_0060.shtml',
        'http://az.lib.ru/t/tolstoj_lew_nikolaewich/text_0070.shtml',
        'http://az.lib.ru/t/tolstoj_lew_nikolaewich/text_0080.shtml',
        'http://az.lib.ru/t/tolstoj_lew_nikolaewich/text_0090.shtml',
        'http://az.lib.ru/t/tolstoj_lew_nikolaewich/text_1860_dekabristy.shtml']

In [14]:
import requests
import re, html

def download(url):
    return requests.get(url).text

# code borrowed from here: https://github.com/pallets/markupsafe/blob/0.23/markupsafe/__init__.py#L21
striptags_re = re.compile(r'(<!--.*?-->|<[^>]*>)')
entity_re = re.compile(r'&([^;]+);')

def to_text(s):
    return html.unescape(striptags_re.sub('',s))

def beautify(s):
    lines = [ x.strip() for x in s.split('\n') if x.strip()!=""]
    for i in range(min(100,len(lines))):
        if lines[i]=='-->':
            break
    return '\n'.join(lines[i+1:] if i<100 else lines)
    
with open('dataset.txt','w',encoding='utf-8') as f:
    for u in urls:
        text = beautify(to_text(download(u)))
        f.write(text+'\n\n')
        

In [1]:
import transformers as tr
import tokenizers as tok

In [2]:
tokenizer = tok.Tokenizer(tok.models.BPE(unk_token='[UNK]'))
tokenizer.pre_tokenizer = tok.pre_tokenizers.Whitespace()
trainer = tok.trainers.BpeTrainer(special_tokens=["[UNK]", "[CLS]", "[SEP]", "[PAD]", "[MASK]","[EOS]"])
tokenizer.train(['dataset.txt'],trainer)
tokenizer.enable_padding()

Failed to deserialize variable 'tokenizer'. Run the following code to delete it:
  del_datasphere_variables('dataset', 'ds', 'dsb', 'gpt', 'targs', 'tokenizer', 'trainer', 'ttokenizer')
Traceback (most recent call last):
  File "/kernel/lib/python3.10/site-packages/ml_kernel/state/state_protocol.py", line 283, in _load_component
    value = unpickler.load()
  File "/home/jupyter/.local/lib/python3.10/site-packages/datasets/table.py", line 1069, in __setstate__
    table = _memory_mapped_arrow_table_from_file(path)
  File "/home/jupyter/.local/lib/python3.10/site-packages/datasets/table.py", line 65, in _memory_mapped_arrow_table_from_file
    opened_stream = _memory_mapped_record_batch_reader_from_file(filename)
  File "/home/jupyter/.local/lib/python3.10/site-packages/datasets/table.py", line 50, in _memory_mapped_record_batch_reader_from_file
    memory_mapped_stream = pa.memory_map(filename)
  File "pyarrow/io.pxi", line 898, in pyarrow.lib.memory_map
  File "pyarrow/io.pxi", line 8

In [3]:
tokenizer.encode('Иван Сигизмундович подошел к окну и закашлялся. Вечерело.').tokens

['Иван',
 'С',
 'иг',
 'изму',
 'н',
 'до',
 'вич',
 'подошел',
 'к',
 'окну',
 'и',
 'закашлялся',
 '.',
 'Вечер',
 'ело',
 '.']

In [4]:
tokenizer.post_processor = tok.processors.TemplateProcessing(
    single="[CLS] $A [SEP]",
    pair="[CLS] $A [SEP] $B:1 [SEP]:1",
    special_tokens=[
        ("[CLS]", tokenizer.token_to_id("[CLS]")),
        ("[SEP]", tokenizer.token_to_id("[SEP]")),
    ],
)

In [5]:
tokenizer.encode('Иван Сигизмундович подошел к окну и закашлялся.','Вечерело.').tokens

['[CLS]',
 'Иван',
 'С',
 'иг',
 'изму',
 'н',
 'до',
 'вич',
 'подошел',
 'к',
 'окну',
 'и',
 'закашлялся',
 '.',
 '[SEP]',
 'Вечер',
 'ело',
 '.',
 '[SEP]']

In [6]:
vocab = tokenizer.get_vocab()
len(vocab)

30000

In [7]:
config = tr.GPT2Config(
    vocab_size=len(vocab),
    bos_token_id=tokenizer.token_to_id('[CLS]'),
    eos_token_id=tokenizer.token_to_id('[EOS]'))
gpt = tr.GPT2LMHeadModel(config)

/usr/local/lib/python3.10/dist-packages/torch/cuda/__init__.py:546: UserWarning: Can't initialize NVML
  warnings.warn("Can't initialize NVML")


In [8]:
ttokenizer = tr.PreTrainedTokenizerFast(tokenizer_object=tokenizer)
#ttokenizer=tr.AutoTokenizer.from_pretrained("openai-gpt")
res = gpt.generate(**ttokenizer("[CLS]Мне нравится ",return_tensors="pt"),max_new_tokens=50)
ttokenizer.decode(res[0])

Setting `pad_token_id` to `eos_token_id`:5 for open-end generation.


'[CLS] [CLS] Мне нравится [SEP] растения растения растения растения растения растения растения растения растения опре опре опре опре опре опре опре опре опре опре опре опре опре опре воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание воззвание голосами голосами голосами голосами голосами голосами Огля Огля'

In [9]:
import datasets

In [10]:
#!g1.1
dataset = datasets.load_dataset("text",data_files="dataset.txt")
dataset['train'][13]

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

{'text': 'Он взял своею большою рукой меня за руку, и пожал так крепко, честно, только что не больно. Я думала, что он поцелует мою руку, и нагнулась было к нему, но он еще раз пожал мне руку и прямо в глаза посмотрел своим твердым и веселым взглядом.'}

In [11]:
#!g1.1
def tokenize(x):
    x = ttokenizer(x['text'])
    x['labels'] = x['input_ids'].copy()
    return x

ds = dataset.map(tokenize, batched=True, remove_columns=['text'])
ds['train'][0]

Parameter 'function'=<function tokenize at 0x7f01b4181990> of the transform datasets.arrow_dataset.Dataset._map_single couldn't be hashed properly, a random hash was used instead. Make sure your transforms and parameters are serializable with pickle or dill for the dataset fingerprinting and caching to work. If you reuse this transform, the caching mechanism will consider it to be different from the previous calls and recompute everything. This warning is only showed once. Subsequent hashing failures won't be showed.


Map:   0%|          | 0/60779 [00:00<?, ? examples/s]

{'input_ids': [1, 9590, 9740, 3197, 2],
 'token_type_ids': [0, 0, 0, 0, 0],
 'attention_mask': [1, 1, 1, 1, 1],
 'labels': [1, 9590, 9740, 3197, 2]}

In [12]:
#!g1.1
from itertools import chain 

block_size=512

def group_texts(examples):
    # Concatenate all texts.
    concatenated_examples = {k: list(chain(*examples[k])) for k in examples.keys()}
    total_length = len(concatenated_examples[list(examples.keys())[0]])
    total_length = (total_length // block_size) * block_size
    result = {
        k: [t[i : i + block_size] for i in range(0, total_length, block_size)]
        for k, t in concatenated_examples.items()
    }
    result["labels"] = result["input_ids"].copy()
    return result

dsb = ds.map(group_texts,batched=True)

Map:   0%|          | 0/60779 [00:00<?, ? examples/s]

In [13]:
#!g1.1
targs = tr.TrainingArguments(
    output_dir = 'gpt2-scratch',
    num_train_epochs=15,
    learning_rate=1e-5
)
trainer = tr.Trainer(gpt,args=targs,
    train_dataset=dsb['train'],
    tokenizer=ttokenizer,
    data_collator=tr.default_data_collator #tr.DataCollatorForLanguageModeling(tokenizer=ttokenizer,mlm=False)
)

2023-10-24 06:12:43.150309: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [14]:
#!g1.1
ds['train'][0]

{'input_ids': [1, 9590, 9740, 3197, 2],
 'token_type_ids': [0, 0, 0, 0, 0],
 'attention_mask': [1, 1, 1, 1, 1],
 'labels': [1, 9590, 9740, 3197, 2]}

In [15]:
#!g1.1
trainer.train()

OSError: [Errno 28] No space left on device

In [22]:
#!g1.1
ttokenizer = tr.PreTrainedTokenizerFast(tokenizer_object=tokenizer)
res = gpt.generate(**ttokenizer("[CLS]Пьер посмотрел на ",return_tensors="pt").to("cuda"),max_new_tokens=50)
ttokenizer.decode(res[0])

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:5 for open-end generation.


AttributeError: 'str' object has no attribute 'shape'

In [ ]:
#!g1.1
